
# Examples for constraint aggregation


In [ ]:
from __future__ import annotations

from copy import deepcopy

from gemseo import configure_logger
from gemseo import create_scenario
from gemseo.algos.design_space import DesignSpace
from gemseo.disciplines.analytic import AnalyticDiscipline
from gemseo.disciplines.concatenater import Concatenater

configure_logger()

Number of constraints



In [ ]:
N = 100

Build the discipline



In [ ]:
constraint_names = [f"g_{k + 1}" for k in range(N)]
function_names = ["o", *constraint_names]
function_expressions = ["y"] + [f"{k + 1}*x*exp(1-{k + 1}*x)-y" for k in range(N)]
disc = AnalyticDiscipline(
    name="function",
    expressions=dict(zip(function_names, function_expressions)),
)
# This step is required to put all constraints needed for aggregation in one variable.
concat = Concatenater(constraint_names, "g")

Build the design space



In [ ]:
ds = DesignSpace()
ds.add_variable(
    "x",
    l_b=0.0,
    u_b=1,
    value=1.0 / N / 2.0,
    var_type=DesignSpace.DesignVariableType.FLOAT,
)
ds.add_variable(
    "y", l_b=0.0, u_b=1, value=1, var_type=DesignSpace.DesignVariableType.FLOAT
)

ds_new = deepcopy(ds)

Build the optimization solver options



In [ ]:
max_iter = 1000
ineq_tol = 1e-5
convergence_tol = 1e-8
normalize = True
algo_options = {
    "algo": "NLOPT_MMA",
    "max_iter": max_iter,
    "algo_options": {
        "ineq_tolerance": ineq_tol,
        "eq_tolerance": ineq_tol,
        "xtol_rel": convergence_tol,
        "xtol_abs": convergence_tol,
        "ftol_rel": convergence_tol,
        "ftol_abs": convergence_tol,
        "ctol_abs": convergence_tol,
        "normalize_design_space": normalize,
    },
}

Build the optimization scenario



In [ ]:
original_scenario = create_scenario(
    [disc, concat],
    "DisciplinaryOpt",
    "o",
    ds,
    maximize_objective=False,
)
original_scenario.add_constraint("g", constraint_type="ineq")

original_scenario.execute(algo_options)
# Without constraint aggregation MMA iterations become more expensive, when a
# large number of constraints are activated.

exploiting constraint aggregation on the same scenario:



In [ ]:
new_scenario = create_scenario(
    [disc, concat],
    "DisciplinaryOpt",
    "o",
    ds_new,
    maximize_objective=False,
)
new_scenario.add_constraint("g", constraint_type="ineq")

This method aggregates the constraints using the lower bound KS function



In [ ]:
new_scenario.formulation.opt_problem.aggregate_constraint(
    0, method="lower_bound_KS", rho=10.0
)
new_scenario.execute(algo_options)

with constraint aggregation the last iteration is faster.

